<a href="https://colab.research.google.com/github/A01793146/demodatabricks/blob/main/benja.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [1]:
from sklearn.decomposition import PCA
from sklearn.preprocessing import StandardScaler
from sklearn.model_selection import train_test_split
from sklearn.preprocessing import OneHotEncoder
from sklearn.cluster import KMeans

import matplotlib.pyplot as plt
from mpl_toolkits.mplot3d import Axes3D

import pandas as pd
from sklearn.linear_model import LogisticRegression
from sklearn.metrics import accuracy_score
import matplotlib.pyplot as plt
import warnings
warnings.filterwarnings('ignore')

In [2]:
df= pd.read_csv(r"marketing_campaign-vdev.csv")

dfPerson = df[["Year_Birth","Education", "Marital_Status", "Income", "Kidhome", "Teenhome"]]

dfSales = df[["Year_Birth","Education", "Marital_Status", "Income", "Kidhome", "Teenhome",
              "Ticket", "MAU", "Device", "QY"]]

dfEvent = df[["Year_Birth","Education", "Marital_Status", "Income", "Kidhome", "Teenhome", "Dt_Customer",
              "Ticket", "MAU", "Device", "QY", "Store Only", "Online Only", "Store-Online", "Event"]]

dfPerson.head()




Year_Birth   Education Marital_Status   Income  Kidhome  Teenhome
0        1969         PhD        Married  90-99 K        0         2
1        1973  Graduation       Divorced  70-79 K        0         1
2        1976  Graduation          OTHER  70-79 K        0         1
3        1974  Graduation         Single  60-69 K        0         0
4        1976         PhD       Divorced  60-69 K        0         1

In [3]:
dfSales.head()


Year_Birth   Education Marital_Status   Income  Kidhome  Teenhome  Ticket  \
0        1969         PhD        Married  90-99 K        0         2      99   
1        1973  Graduation       Divorced  70-79 K        0         1      99   
2        1976  Graduation          OTHER  70-79 K        0         1      99   
3        1974  Graduation         Single  60-69 K        0         0      99   
4        1976         PhD       Divorced  60-69 K        0         1      99   

   MAU Device   QY  
0    8     HI  Q-3  
1    6     HI  Q-2  
2    5     HI  Q-1  
3    6     HI  Q-2  
4    6     HI  Q-2

In [4]:
dfEvent.head()


Year_Birth   Education Marital_Status   Income  Kidhome  Teenhome  \
0        1969         PhD        Married  90-99 K        0         2   
1        1973  Graduation       Divorced  70-79 K        0         1   
2        1976  Graduation          OTHER  70-79 K        0         1   
3        1974  Graduation         Single  60-69 K        0         0   
4        1976         PhD       Divorced  60-69 K        0         1   

  Dt_Customer  Ticket  MAU Device   QY  Store Only  Online Only  Store-Online  \
0    01/09/12      99    8     HI  Q-3           0            1             0   
1    17/09/13      99    6     HI  Q-2           0            0             1   
2    27/06/14      99    5     HI  Q-1           0            0             1   
3    26/05/14      99    6     HI  Q-2           0            1             0   
4    07/03/13      99    6     HI  Q-2           0            0             1   

              Event  
0  National Holiday  
1  National Holiday  
2  National Holiday  
3  National Holiday  
4  National Holiday

# Adding socialdemographics

In [5]:
df = pd.DataFrame(dfPerson)
# Step 2: Encoding Categorical Variables
encoder = OneHotEncoder()
encoded_cats = encoder.fit_transform(df[['Education', 'Income', 'Marital_Status']]).toarray()
encoded_feature_names = encoder.get_feature_names_out(['Education', 'Income', 'Marital_Status'])

# Creating a dataframe with the encoded features
encoded_df = pd.DataFrame(encoded_cats, columns=encoded_feature_names)

# Adding the numerical features to the encoded dataframe
for feature in ['Year_Birth',  'Kidhome', 'Teenhome']:
    encoded_df[feature] = df[feature]

scaler = StandardScaler()
scaled_features = scaler.fit_transform(encoded_df)
kmeans = KMeans(n_clusters=3, random_state=42)
df['Cluster'] = kmeans.fit_predict(scaled_features)

pca = PCA(n_components=2)
principal_components = pca.fit_transform(scaled_features)
df_pca = pd.DataFrame(principal_components, columns=['PC1', 'PC2'])

# Adding PCA components and cluster info to the original dataframe
df['PC1'] = df_pca['PC1']
df['PC2'] = df_pca['PC2']

# Plotting with Plotly
fig = px.scatter(df, x='PC1', y='PC2',
                 color='Cluster',
                 hover_data=['Year_Birth', 'Education', 'Marital_Status', 'Income', 'Kidhome', 'Teenhome'],
                 title="K-means Clustering Results with PCA")

fig.show()

NameError: name 'px' is not defined

In [ ]:
import plotly.graph_objects as go


scaler = StandardScaler()
scaled_features = scaler.fit_transform(encoded_df)
kmeans = KMeans(n_clusters=3, random_state=42)
df['Cluster'] = kmeans.fit_predict(scaled_features)
pca = PCA(n_components=3)  # Change to 3 components for 3D plot
principal_components = pca.fit_transform(scaled_features)
df_pca = pd.DataFrame(principal_components, columns=['PC1', 'PC2', 'PC3'])

# Adding PCA components and cluster info to the original dataframe
df['PC1'] = df_pca['PC1']
df['PC2'] = df_pca['PC2']
df['PC3'] = df_pca['PC3']
# Create hover text for each point
hover_text = []
for index, row in df.iterrows():
    hover_text.append(
        f'Year Birth: {row["Year_Birth"]}<br>' +
        f'Education: {row["Education"]}<br>' +
        f'Marital Status: {row["Marital_Status"]}<br>' +
        f'Income: {row["Income"]}<br>' +
        f'Kidhome: {row["Kidhome"]}<br>' +
        f'Teenhome: {row["Teenhome"]}<br>' +
        f'Cluster: {row["Cluster"]}'
    )

# Plotting with Plotly
fig = go.Figure(data=[go.Scatter3d(
    x=df['PC1'],
    y=df['PC2'],
    z=df['PC3'],
    mode='markers',
    marker=dict(
        size=3,  # Adjust the size here
        color=df['Cluster'],  # Color by cluster
        opacity=0.8,
        colorscale='Viridis'  # Change color scale if needed
    ),
    text=hover_text,
    hoverinfo='text'
)])

fig.update_layout(title='K-means Clustering Results with PCA (3D)',
                  scene=dict(
                      xaxis_title='PC1',
                      yaxis_title='PC2',
                      zaxis_title='PC3'
                  ))

fig.show()

In [ ]:
# t-SNE for dimensionality reduction
tsne = TSNE(n_components=3, random_state=42)
tsne_components = tsne.fit_transform(scaled_features)
df_tsne = pd.DataFrame(tsne_components, columns=['TSNE1', 'TSNE2', 'TSNE3'])

# Adding t-SNE components and cluster info to the original dataframe
df['TSNE1'] = df_tsne['TSNE1']
df['TSNE2'] = df_tsne['TSNE2']
df['TSNE3'] = df_tsne['TSNE3']

# Plotting with Plotly
fig = go.Figure(data=[go.Scatter3d(
    x=df['TSNE1'],
    y=df['TSNE2'],
    z=df['TSNE3'],
    mode='markers',
    marker=dict(
        size=3,  # Adjust the size here
        color=df['Cluster'],  # Color by cluster
        opacity=0.8,
        colorscale='Viridis'  # Change color scale if needed
    ),
    text=df[['Year_Birth', 'Education', 'Marital_Status', 'Income', 'Kidhome', 'Teenhome']],
    hoverinfo='text'
)])

fig.update_layout(title='K-means Clustering Results with t-SNE (3D)',
                  scene=dict(
                      xaxis_title='TSNE1',
                      yaxis_title='TSNE2',
                      zaxis_title='TSNE3'
                  ))

fig.show()

# Adding Sales Behavior

In [ ]:
df = pd.DataFrame(dfSales)
# Step 2: Encoding Categorical Variables
encoder = OneHotEncoder()
encoded_cats = encoder.fit_transform(df[['Education', 'Income', 'Marital_Status', 'Device', 'QY']]).toarray()
encoded_feature_names = encoder.get_feature_names_out(['Education', 'Income', 'Marital_Status', 'Device', 'QY'])

# Creating a dataframe with the encoded features
encoded_df = pd.DataFrame(encoded_cats, columns=encoded_feature_names)

# Adding the numerical features to the encoded dataframe
for feature in ['Year_Birth',  'Kidhome', 'Teenhome', 'Ticket', 'MAU']:
    encoded_df[feature] = df[feature]

scaler = StandardScaler()
scaled_features = scaler.fit_transform(encoded_df)
kmeans = KMeans(n_clusters=5, random_state=42)
df['Cluster'] = kmeans.fit_predict(scaled_features)
pca = PCA(n_components=2)
principal_components = pca.fit_transform(scaled_features)
df_pca = pd.DataFrame(principal_components, columns=['PC1', 'PC2'])

# Adding PCA components and cluster info to the original dataframe
df['PC1'] = df_pca['PC1']
df['PC2'] = df_pca['PC2']

# Plotting with Plotly
fig = px.scatter(df, x='PC1', y='PC2',
                 color='Cluster',
                 hover_data=['Year_Birth', 'Education', 'Marital_Status', 'Income', 'Kidhome', 'Teenhome', 'Device', 'QY'],
                 title="K-means Clustering Results with PCA")

fig.show()

In [ ]:

scaler = StandardScaler()
scaled_features = scaler.fit_transform(encoded_df)
kmeans = KMeans(n_clusters=3, random_state=42)
df['Cluster'] = kmeans.fit_predict(scaled_features)
pca = PCA(n_components=3)  # Change to 3 components for 3D plot
principal_components = pca.fit_transform(scaled_features)
df_pca = pd.DataFrame(principal_components, columns=['PC1', 'PC2', 'PC3'])

# Adding PCA components and cluster info to the original dataframe
df['PC1'] = df_pca['PC1']
df['PC2'] = df_pca['PC2']
df['PC3'] = df_pca['PC3']
# Create hover text for each point
hover_text = []
for index, row in df.iterrows():
    hover_text.append(
        f'Year Birth: {row["Year_Birth"]}<br>' +
        f'Education: {row["Education"]}<br>' +
        f'Marital Status: {row["Marital_Status"]}<br>' +
        f'Income: {row["Income"]}<br>' +
        f'Kidhome: {row["Kidhome"]}<br>' +
        f'Teenhome: {row["Teenhome"]}<br>' +
        f'Ticket: {row["Ticket"]}<br>' +
        f'MAU: {row["MAU"]}<br>' +
        f'Device: {row["Device"]}<br>' +

        f'Cluster: {row["Cluster"]}'
    )

# Plotting with Plotly
fig = go.Figure(data=[go.Scatter3d(
    x=df['PC1'],
    y=df['PC2'],
    z=df['PC3'],
    mode='markers',
    marker=dict(
        size=3,  # Adjust the size here
        color=df['Cluster'],  # Color by cluster
        opacity=0.8,
        colorscale='Viridis'  # Change color scale if needed
    ),
    text=hover_text,
    hoverinfo='text'
)])

fig.update_layout(title='K-means Clustering Results with PCA (3D)',
                  scene=dict(
                      xaxis_title='PC1',
                      yaxis_title='PC2',
                      zaxis_title='PC3'
                  ))

fig.show()

In [ ]:
# t-SNE for dimensionality reduction
tsne = TSNE(n_components=3, random_state=42)
tsne_components = tsne.fit_transform(scaled_features)
df_tsne = pd.DataFrame(tsne_components, columns=['TSNE1', 'TSNE2', 'TSNE3'])

# Adding t-SNE components and cluster info to the original dataframe
df['TSNE1'] = df_tsne['TSNE1']
df['TSNE2'] = df_tsne['TSNE2']
df['TSNE3'] = df_tsne['TSNE3']

# Create text information for hover
df['Hover_Text'] = df[['Year_Birth', 'Education', 'Marital_Status', 'Income', 'Kidhome', 'Teenhome']].astype(str).agg('<br>'.join, axis=1)

# Plotting with Plotly
fig = go.Figure(data=[go.Scatter3d(
    x=df['TSNE1'],
    y=df['TSNE2'],
    z=df['TSNE3'],
    mode='markers',
    marker=dict(
        size=3,  # Adjust the size here
        color=df['Cluster'],  # Color by cluster
        opacity=0.8,
        colorscale='Viridis'  # Change color scale if needed
    ),
    text=df['Hover_Text'],
    hoverinfo='text'
)])

fig.update_layout(title='K-means Clustering Results with t-SNE (3D)',
                  scene=dict(
                      xaxis_title='TSNE1',
                      yaxis_title='TSNE2',
                      zaxis_title='TSNE3'
                  ))

fig.show()

# Adding Event Behavior

In [ ]:
df = pd.DataFrame(dfEvent)
# Step 2: Encoding Categorical Variables
encoder = OneHotEncoder()
encoded_cats = encoder.fit_transform(df[['Education', 'Income', 'Marital_Status', 'Device', 'QY','Event']]).toarray()
encoded_feature_names = encoder.get_feature_names_out(['Education', 'Income', 'Marital_Status', 'Device', 'QY', 'Event'])

# Creating a dataframe with the encoded features
encoded_df = pd.DataFrame(encoded_cats, columns=encoded_feature_names)

# Adding the numerical features to the encoded dataframe
for feature in ['Year_Birth',  'Kidhome', 'Teenhome', 'Ticket', 'MAU', 'Store Only', 'Online Only', 'Store-Online']:
    encoded_df[feature] = df[feature]

scaler = StandardScaler()


scaled_features = scaler.fit_transform(encoded_df)
kmeans = KMeans(n_clusters=8, random_state=42)
df['Cluster'] = kmeans.fit_predict(scaled_features)
pca = PCA(n_components=2)
principal_components = pca.fit_transform(scaled_features)
df_pca = pd.DataFrame(principal_components, columns=['PC1', 'PC2'])

# Adding PCA components and cluster info to the original dataframe
df['PC1'] = df_pca['PC1']
df['PC2'] = df_pca['PC2']

# Plotting with Plotly
fig = px.scatter(df, x='PC1', y='PC2',
                 color='Cluster',
                 hover_data=['Year_Birth', 'Education', 'Marital_Status', 'Income', 'Kidhome', 'Teenhome', 'Device', 'QY', 'Store Only', 'Online Only', 'Store-Online'],
                 title="K-means Clustering Results with PCA")

fig.show()

In [ ]:
scaler = StandardScaler()
scaled_features = scaler.fit_transform(encoded_df)
kmeans = KMeans(n_clusters=3, random_state=42)
df['Cluster'] = kmeans.fit_predict(scaled_features)
pca = PCA(n_components=3)  # Change to 3 components for 3D plot
principal_components = pca.fit_transform(scaled_features)
df_pca = pd.DataFrame(principal_components, columns=['PC1', 'PC2', 'PC3'])

# Adding PCA components and cluster info to the original dataframe
df['PC1'] = df_pca['PC1']
df['PC2'] = df_pca['PC2']
df['PC3'] = df_pca['PC3']
# Create hover text for each point
hover_text = []
for index, row in df.iterrows():
    hover_text.append(
        f'Year Birth: {row["Year_Birth"]}<br>' +
        f'Education: {row["Education"]}<br>' +
        f'Marital Status: {row["Marital_Status"]}<br>' +
        f'Income: {row["Income"]}<br>' +
        f'Kidhome: {row["Kidhome"]}<br>' +
        f'Teenhome: {row["Teenhome"]}<br>' +
        f'Ticket: {row["Ticket"]}<br>' +
        f'MAU: {row["MAU"]}<br>' +
        f'Device: {row["Device"]}<br>' +
        f'Event: {row["Event"]}<br>' +
        f'Store Only: {row["Store Only"]}<br>' +
        f'Online Only: {row["Online Only"]}<br>' +
        f'Store-Online: {row["Store-Online"]}<br>' +

        f'Cluster: {row["Cluster"]}'
    )

# Plotting with Plotly
fig = go.Figure(data=[go.Scatter3d(
    x=df['PC1'],
    y=df['PC2'],
    z=df['PC3'],
    mode='markers',
    marker=dict(
        size=3,  # Adjust the size here
        color=df['Cluster'],  # Color by cluster
        opacity=0.8,
        colorscale='Viridis'  # Change color scale if needed
    ),
    text=hover_text,
    hoverinfo='text'
)])

fig.update_layout(title='K-means Clustering Results with PCA (3D)',
                  scene=dict(
                      xaxis_title='PC1',
                      yaxis_title='PC2',
                      zaxis_title='PC3'
                  ))

fig.show()

In [ ]:
# t-SNE for dimensionality reduction
tsne = TSNE(n_components=3, random_state=42)
tsne_components = tsne.fit_transform(scaled_features)
df_tsne = pd.DataFrame(tsne_components, columns=['TSNE1', 'TSNE2', 'TSNE3'])

# Adding t-SNE components and cluster info to the original dataframe
df['TSNE1'] = df_tsne['TSNE1']
df['TSNE2'] = df_tsne['TSNE2']
df['TSNE3'] = df_tsne['TSNE3']

# Create text information for hover
df['Hover_Text'] = df[['Event']].astype(str).agg('<br>'.join, axis=1)

# Plotting with Plotly
fig = go.Figure(data=[go.Scatter3d(
    x=df['TSNE1'],
    y=df['TSNE2'],
    z=df['TSNE3'],
    mode='markers',
    marker=dict(
        size=3,  # Adjust the size here
        color=df['Cluster'],  # Color by cluster
        opacity=0.8,
        colorscale='Viridis'  # Change color scale if needed
    ),
    text=df['Hover_Text'],
    hoverinfo='text'
)])

fig.update_layout(title='K-means Clustering Results with t-SNE (3D)',
                  scene=dict(
                      xaxis_title='TSNE1',

                      yaxis_title='TSNE2',
                      zaxis_title='TSNE3'
                  ))

fig.show()

In [ ]:
import hdbscan
from sklearn.mixture import GaussianMixture


df = pd.DataFrame(dfEvent)

# Preprocessing
encoder = OneHotEncoder()
encoded_cats = encoder.fit_transform(df[['Education', 'Marital_Status', 'Income']]).toarray()
encoded_feature_names = encoder.get_feature_names_out(['Education', 'Marital_Status', 'Income'])
encoded_df = pd.DataFrame(encoded_cats, columns=encoded_feature_names)
for feature in ['Year_Birth', 'Kidhome', 'Teenhome']:
    encoded_df[feature] = df[feature]
scaler = StandardScaler()
scaled_features = scaler.fit_transform(encoded_df)

# Dimensionality reduction with t-SNE
tsne = TSNE(n_components=2, random_state=42)
tsne_components = tsne.fit_transform(scaled_features)
df['TSNE1'] = tsne_components[:, 0]  # Adding t-SNE components to the original dataframe
df['TSNE2'] = tsne_components[:, 1]

# Creating Gaussian Mixture Model
gmm = GaussianMixture(n_components=3, random_state=42)
df['Cluster'] = gmm.fit_predict(scaled_features)

# Create text information for hover
df['Hover_Text'] = df[['Year_Birth', 'Education', 'Marital_Status', 'Income', 'Kidhome', 'Teenhome']].astype(str).agg('<br>'.join, axis=1)

# Plotting with Plotly
fig = go.Figure(data=[go.Scatter(
    x=df['TSNE1'],
    y=df['TSNE2'],
    mode='markers',
    marker=dict(
        size=8,  # Adjust the size here
        color=df['Cluster'],  # Color by cluster
        opacity=0.8,
        colorscale='Viridis'  # Change color scale if needed
    ),
    text=df['Hover_Text'],
    hoverinfo='text'
)])

fig.update_layout(title='Gaussian Mixture Model Clustering Results with t-SNE (2D)',
                  xaxis_title='TSNE1',
                  yaxis_title='TSNE2')

fig.show()

     ---------------------------------------- 5.2/5.2 MB 8.7 MB/s eta 0:00:00
  Installing build dependencies: started
  Installing build dependencies: finished with status 'done'
  Getting requirements to build wheel: started
  Getting requirements to build wheel: finished with status 'done'
  Preparing metadata (pyproject.toml): started
  Preparing metadata (pyproject.toml): finished with status 'done'
  Using cached Cython-0.29.37-py2.py3-none-any.whl (989 kB)
  Created wheel for hdbscan: filename=hdbscan-0.8.33-cp38-cp38-win_amd64.whl size=612508 sha256=2479dd332baefbc042deb288a08be297b845b928ab3b7a105b840d7f3713aeda
  Stored in directory: c:\users\52552\appdata\local\pip\cache\wheels\72\93\36\3c7c74a6f2127e71810a0e0f535955175556a434aec55de679
Successfully built hdbscan
  Attempting uninstall: cython
    Found existing installation: Cython 3.0.6
    Uninstalling Cython-3.0.6:
      Successfully uninstalled Cython-3.0.6
